# A full business solution
## Now we will take our project from Day 1 to the next level
## BUSINESS CHALLENGE:
Create a product that builds a Brochure for a company to be used for prospective clients, investors and potential recruits.

We will be provided a company name and their primary website.

See the end of this notebook for examples of real-world business applications.

And remember: I'm always available if you have problems or ideas! Please do reach out.

In [2]:
#imports 

import os
import requests
import json
from typing import List
from dotenv import load_dotenv
from bs4 import BeautifulSoup
from IPython.display import Markdown, display, update_display
from openai import OpenAI

In [3]:
# Initialize and constants

load_dotenv()
api_key=os.getenv('OPENAI_API_KEY')

if api_key and api_key[:8]=='sk-proj-':
    print("API key looks good so far")
else:
    print("There might be a problem with your API key? ")

MODEL='gpt-4o-mini'
openai=OpenAI()


API key looks good so far


In [4]:
# A class to represent a Webpage

class Website:
    """
    A utility class to represent a Website that we have scraped, now with links
    """

    def __init__(self, url):
        self.url = url
        response = requests.get(url)
        self.body = response.content
        soup = BeautifulSoup(self.body, 'html.parser')
        self.title = soup.title.string if soup.title else "No title found"
        if soup.body:
            for irrelevant in soup.body(["script", "style", "img", "input"]):
                irrelevant.decompose()
            self.text = soup.body.get_text(separator="\n", strip=True)
        else:
            self.text = ""
        links = [link.get('href') for link in soup.find_all('a')]
        self.links = [link for link in links if link]

    def get_contents(self):
        return f"Webpage Title:\n{self.title}\nWebpage Contents:\n{self.text}\n\n"

In [ ]:
ed=Website("https://www.anthropic.com/")
print(ed.get_contents)
ed.links

## First step: Have GPT-4o-mini figure out which links are relevant

### Use a call to gpt-4o-mini to read the links on a webpage, and respond in structured JSON.  
It should decide which links are relevant, and replace relative links such as "/about" with "https://company.com/about".  
We will use "one shot prompting" in which we provide an example of how it should respond in the prompt.

This is an excellent use case for an LLM, because it requires nuanced understanding. Imagine trying to code this without LLMs by parsing and analyzing the webpage - it would be very hard!

Sidenote: there is a more advanced technique called "Structured Outputs" in which we require the model to respond according to a spec. We cover this technique in Week 8 during our autonomous Agentic AI project.

In [5]:
link_system_prompt="You are provided with a list of links found on a webpage. \
You are able to decide which of the links would be most relevant to include in a brochure about the company, \
such as links to an About page, or a Company page, or Careers/Jobs pages.\n"
link_system_prompt+="You should respond in JSON as in this example:"
link_system_prompt+="""
{
    "links":[
        {"type": "about page", "url": "https://full.url/goes/here/about"},
        {"type": "careers page": "url": "https://another.full.url/careers"}
    ]
}
"""

In [ ]:
print(link_system_prompt)

In [6]:
def get_links_user_prompt(website):
    user_prompt = f"Here is the list of links on the website of {website.url} - "
    user_prompt += "please decide which of these are relevant web links for a brochure about the company, respond with the full https URL in JSON format. \
Do not include Terms of Service, Privacy, email links.\n"
    user_prompt += "Links (some might be relative links):\n"
    user_prompt += "\n".join(website.links)
    return user_prompt

In [ ]:
print(get_links_user_prompt(ed))

In [7]:
def get_links(url):
    website=Website(url)
    response=openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": link_system_prompt},
            {"role": "user", "content": get_links_user_prompt(website)}
      ],
        response_format={"type":"json_object"}
    )
    result=response.choices[0].message.content
    return json.loads(result)

In [ ]:
anthropic=Website("https://www.anthropic.com/")
anthropic.links

In [ ]:
get_links("https://www.anthropic.com/")

## Second step: make the brochure!

Assemble all the details into another prompt to GPT4-o

In [8]:
def get_all_details(url):
    result="Landing page:\n"
    result+=Website(url).get_contents()
    links=get_links(url)
    print("Found links:",links)
    for link in links["links"]:
        result+=f"\n\n{link['type']}\n"
        result+=Website(link["url"]).get_contents()
    return result

In [ ]:
print(get_all_details("https://anthropic.com"))

In [9]:
system_prompt = "You are an assistant that analyzes the contents of several relevant pages from a company website \
and creates a short brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
Include details of company culture, customers and careers/jobs if you have the information."

# Or uncomment the lines below for a more humorous brochure - this demonstrates how easy it is to incorporate 'tone':

# system_prompt = "You are an assistant that analyzes the contents of several relevant pages from a company website \
# and creates a short humorous, entertaining, jokey brochure about the company for prospective customers, investors and recruits. Respond in markdown.\
# Include details of company culture, customers and careers/jobs if you have the information."


In [10]:
def get_brochure_user_prompt(company_name, url):
    user_prompt = f"You are looking at a company called: {company_name}\n"
    user_prompt += f"Here are the contents of its landing page and other relevant pages; use this information to build a short brochure of the company in markdown.\n"
    user_prompt += get_all_details(url)
    user_prompt = user_prompt[:20_000] # Truncate if more than 20,000 characters
    return user_prompt

In [ ]:
get_brochure_user_prompt("Anthropic", "https://anthropic.com")

In [11]:
def create_brochure(company_name, url):
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(company_name, url)}
          ],
    )
    result = response.choices[0].message.content
    display(Markdown(result))

In [ ]:
create_brochure("Anthropic", "https://anthropic.com")

## Finally - a minor improvement

With a small adjustment, we can change this so that the results stream back from OpenAI,
with the familiar typewriter animation

In [12]:
def stream_brochure(company_name, url):
    stream= openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": system_prompt},
            {"role": "user", "content": get_brochure_user_prompt(company_name, url)}
          ],
        stream=True
    )

    response=""
    display_handle=display(Markdown(""),display_id=True)
    for chunk in stream:
        response +=chunk.choices[0].delta.content or ''
        response = response.replace("```","").replace("markdown","")
        update_display(Markdown(response),display_id=display_handle.display_id)

In [ ]:
stream_brochure("HuggingFace", "http://huggingface.co")

# Convert the brochure to a specified language


In [13]:
def create_brochure_language(company_name, url, language):
    language_prompt = f"You are a professional translator and writer specializing in creating and translating brochures. Convert the brochure to {language} while maintaining its original tone, format, and purpose."
    user_language_prompt = f"Generate a brochure for the company '{company_name}' available at the URL: {url}, and translate it into {language}."
    response = openai.chat.completions.create(
        model=MODEL,
        messages=[
            {"role": "system", "content": language_prompt},
            {"role": "user", "content": user_language_prompt}
        ],
    )
    result = response.choices[0].message.content
    display(Markdown(result))


In [14]:
create_brochure_language("HuggingFace", "http://huggingface.co","Hindi")

### HuggingFace Brochure

---

**HuggingFace: Empowering AI with Community and Innovation**

Welcome to HuggingFace! Our mission is to democratize AI by building an open-source ecosystem. Explore our cutting-edge tools, libraries, and models that help developers, researchers, and companies leverage the power of artificial intelligence.

---

#### What We Offer:

1. **Transformers Library**  
   The most popular open-source library for Natural Language Processing (NLP). Easily integrate state-of-the-art models into your applications.

2. **Datasets**  
   Access a wide range of curated datasets for various AI tasks. Perfect for training and evaluating your models.

3. **Model Hub**  
   Explore thousands of pre-trained models. Customize and deploy them to meet your specific needs.

4. **Community Support**  
   Join our vibrant community of developers and researchers. Share knowledge, seek help, and collaborate on fascinating AI projects.

---

#### Why Choose HuggingFace?

- **User-Friendly**  
  Built with developers in mind, our tools are intuitive and easy to use.

- **Extensive Documentation**  
  Comprehensive guides and examples to help you get started quickly.

- **Active Development**  
  We are continuously improving our libraries and models, driven by community feedback.

- **Enterprise Support**  
  Tailored solutions and support for businesses to implement AI strategies effectively.

---

#### Get Started Today!

Visit us at [huggingface.co](http://huggingface.co) to learn more, access our tools, and join the AI revolution.

---

**Contact Us:**  
Email: contact@huggingface.co  
Twitter: @HuggingFace  
Join our community forums to connect with fellow AI enthusiasts!

---

### हिंदी में अनुवादित पैम्फलेट

---

**हगिंगफेस: समुदाय और नवाचार के साथ एआई को सशक्त बनाना**

हगिंगफेस में आपका स्वागत है! हमारा मिशन एक ओपन-सोर्स पारिस्थितिकी तंत्र बनाकर एआई को लोकतांत्रिक बनाना है। हमारे अत्याधुनिक उपकरणों, पुस्तकालयों और मॉडलों का अन्वेषण करें जो डेवलपर्स, शोधकर्ताओं और कंपनियों को कृत्रिम बुद्धिमत्ता की शक्ति का लाभ उठाने में मदद करते हैं।

---

#### हम क्या पेश करते हैं:

1. **ट्रांसफार्मर्स पुस्तकालय**  
   प्राकृतिक भाषा प्रसंस्करण (NLP) के लिए सबसे लोकप्रिय ओपन-सोर्स पुस्तकालय। अपने अनुप्रयोगों में अत्याधुनिक मॉडलों को आसानी से एकीकृत करें।

2. **डेटासेट्स**  
   विभिन्न एआई कार्यों के लिए कुशलतापूर्वक तैयार किए गए डेटासेट्स की विस्तृत श्रृंखला तक पहुंचें। अपने मॉडलों को प्रशिक्षित और मूल्यांकित करने के लिए उपयुक्त।

3. **मॉडल हब**  
   हजारों प्री-ट्रेंड मॉडलों की खोज करें। उन्हें अपनी विशिष्ट आवश्यकताओं को पूरा करने के लिए अनुकूलित और लागू करें।

4. **समुदाय समर्थन**  
   हमारे जीवंत समुदाय में डेवलपर्स और शोधकर्ताओं से जुड़ें। ज्ञान साझा करें, सहायता प्राप्त करें, और दिलचस्प एआई परियोजनाओं पर सहयोग करें।

---

#### हगिंगफेस क्यों चुनें?

- **उपयोगकर्ता के अनुकूल**  
  हमारे उपकरण डेवलपर्स को ध्यान में रखते हुए बनाए गए हैं, जो सहज और उपयोग में आसान हैं।

- **विस्तृत दस्तावेजीकरण**  
  आपको तेजी से शुरुआत करने में मदद करने के लिए व्यापक मार्गदर्शिकाएँ और उदाहरण।

- **सक्रिय विकास**  
  हम लगातार अपने पुस्तकालयों और मॉडलों में सुधार कर रहे हैं, जो समुदाय से प्राप्त फीडबैक पर आधारित हैं।

- **एंटरप्राइज समर्थन**  
  व्यवसायों के लिए एआई रणनीतियों को प्रभावी रूप से लागू करने के लिए अनुकूलित समाधान और समर्थन।

---

#### आज ही शुरुआत करें!

और जानने के लिए [huggingface.co](http://huggingface.co) पर जाएं, हमारे उपकरणों तक पहुंचें, और एआई क्रांति में शामिल हों।

---

**हमसे संपर्क करें:**  
ईमेल: contact@huggingface.co  
ट्विटर: @HuggingFace  
अन्य एआई उत्साही लोगों से जुड़ने के लिए हमारे समुदाय फोरम में शामिल हों!

--- 

This content maintains the original tone and format while accurately translating it into Hindi.